# Class Project - Comorbidity Associations

In [1]:
import pandas as pd
import networkx as nx
import matplotlib.pyplot as plt
import numpy as np
import random as rnd
import pandas as pd
import altair as alt
alt.data_transformers.enable("vegafusion")
import heapq

In [2]:
df_orig = pd.read_csv("comorbidity_odds_matrix.csv")
threshold = 0
adjacency_matrix_df = pd.read_csv('comorbidity_odds_matrix.csv', index_col=0)
edge_list = adjacency_matrix_df.stack().reset_index()
edge_list.columns = ['source', 'target', 'weight']
sorted_edge_list = edge_list.sort_values(by='weight', ascending=False)
top_10_weighted_edges = sorted_edge_list.head(10)
top_10_nodes = pd.unique(top_10_weighted_edges[['source', 'target']].values.ravel('K'))

print("top 10 weighted edges:")
print(top_10_weighted_edges)
print("--------------------------------------------------------------------------")
print("Nodes associated with top 10 weighted edges:")
print(top_10_nodes)

top 10 weighted edges:
                            source                      target    weight
7000      AHRQ_SpinalCordInjury_DT           AHRQ_Paralysis_DT  6.026605
3571            AHRQ_ImmunityDO_DT       AHRQ_OthInfections_DT  5.001760
6248             AHRQ_Paralysis_DT    AHRQ_SpinalCordInjury_DT  4.996151
1213    AHRQ_ChronicUlcerOfSkin_DT    AHRQ_SpinalCordInjury_DT  3.807992
1205    AHRQ_ChronicUlcerOfSkin_DT           AHRQ_Paralysis_DT  3.393637
3717    AHRQ_InfectiveArthritis_DT  AHRQ_ChronicUlcerOfSkin_DT  3.017421
6947      AHRQ_SpinalCordInjury_DT  AHRQ_ChronicUlcerOfSkin_DT  2.910909
6185             AHRQ_Paralysis_DT   AHRQ_CerebrovascularDs_DT  2.838896
6320  AHRQ_PathologicalFracture_DT        AHRQ_Osteoporosis_DT  2.648420
609     AHRQ_BacterialInfection_DT  AHRQ_InfectiveArthritis_DT  2.644675
--------------------------------------------------------------------------
Nodes associated with top 10 weighted edges:
['AHRQ_SpinalCordInjury_DT' 'AHRQ_ImmunityDO_DT' 'AHRQ

In [3]:
# gets rid of the edges with weight less than 0
df_filter = df_orig.iloc[:,1:] 
df_filter = df_filter.where(df_filter > threshold,0) 
df_clean = pd.concat([df_orig.iloc[:,0], df_filter], axis=1)
df_clean.head()


Unnamed: 0  AHRQ_AbdominalHernia_DT  \
0      AHRQ_AbdominalHernia_DT                 0.000000   
1  AHRQ_AcquiredDeformities_DT                 0.000000   
2         AHRQ_AdjustmentDO_DT                 0.070200   
3               AHRQ_Anemia_DT                 0.168454   
4               AHRQ_Asthma_DT                 0.045368   

   AHRQ_AcquiredDeformities_DT  AHRQ_AdjustmentDO_DT  AHRQ_Anemia_DT  \
0                     0.021786                   0.0        0.090966   
1                     0.000000                   0.0        0.000000   
2                     0.138657                   0.0        0.000000   
3                     0.000000                   0.0        0.000000   
4                     0.000000                   0.0        0.000000   

   AHRQ_Asthma_DT  AHRQ_AttentionDeficitDO_DT  AHRQ_BacterialInfection_DT  \
0        0.252191                         0.0                    0.000000   
1        0.024919                         0.0                    0.000000   
2        0.100560                         0.0                    0.000000   
3        0.000000                         0.0                    0.603858   
4        0.000000                         0.0                    0.000000   

   AHRQ_BiliaryTractDs_DT  AHRQ_Burns_DT  ...  NEPEC_MDD_DT  NEPEC_AFBPDX_DT  \
0                0.710723       0.056411  ...           0.0         0.193681   
1                0.000000       0.465003  ...           0.0         0.041082   
2                0.000000       0.359342  ...           0.0         0.000000   
3                0.341700       0.314066  ...           0.0         0.179997   
4                0.000000       0.281069  ...           0.0         0.246626   

   NEPEC_PTSD_DT  NEPEC_DXODep_DT  NEPEC_ANXunsp_DT  NEPEC_ANXgen_DT  \
0       0.218394         0.566455          0.000000              0.0   
1       0.234353         0.495289          0.000000              0.0   
2       0.000000         1.008589          0.173898              0.0   
3       0.000000         0.519196          0.000000              0.0   
4       0.305148         0.590638          0.000000              0.0   

     dmdxDT  cancerdxDT  anomdxDT  genitaldxDT  
0  0.000000    0.098747  0.005116     0.170254  
1  0.000000    0.000000  0.870268     0.021739  
2  0.000000    0.000000  0.000000     0.120009  
3  0.102596    0.148492  0.000000     0.164761  
4  0.000000    0.000000  0.000000     0.000000  

[5 rows x 96 columns]

In [4]:
df_clean.to_csv('cleaned_data.csv', index=False)

In [5]:
csv_file = pd.read_csv('cleaned_data.csv', index_col=0)

G = nx.DiGraph()

for i, row in csv_file.iterrows():
    for j, weight in row.items():
        if weight != 0 :
            G.add_edge(i,j,weight=weight)

rnd.seed()
n = G.order()


In [6]:
def missingness_function(G, rate):
    G_missing = nx.DiGraph()  
    # G_missing.add_nodes_from(G.nodes()) 
    missing_links = []
    add_edge = []
    for u, v, data in G.edges(G,data=True):
        #print("u,v",u,v)
        if np.random.random() > rate:
            G_missing.add_edge(u, v, **data)
        else:
            missing_links.append((u,v))
            
    return missing_links, G_missing

In [7]:
Y,Go= missingness_function(G,0.2)
print(len(Y))

950


In [8]:
def get_candidateEdges(G):
    nonedges= []
    for i in nx.nodes(G):
        for j in nx.nodes(G):
            if i!=j:
                if not G.has_edge(i,j):
                    nonedges.append((i,j))
                if not G.has_edge(j,i):
                    nonedges.append((j,i))
    return nonedges



In [9]:
def baseline_predictor():
    return rnd.uniform(-1,1)

In [10]:
def jaccard_predictor(G, i, j):
    n = G.order()
    numerator = len(set(G.successors(i)).intersection(G.predecessors(j))) # sum of common outgoing i edges and incoming j edges
    denominator = len(set(G.successors(i)).union(G.predecessors(j))) # sum outgoing i and incoming j edges
    
    if denominator == 0:
        return 0.0
    
    return (numerator / denominator) +  rnd.uniform(0,1/(10*n))

    

In [11]:
def degree_product(G, i, j):
    n = G.order()
    degree_prod = G.out_degree(i) * G.in_degree(j)
    score = degree_prod +  rnd.uniform(0,1/(10*n)) 
    return score

In [12]:
def dijkstra_predictor(G,i,j,flag):
    distances = {node: float('inf') for node in G.nodes()} # dist. between i and everything else
    distances[i] = 0
    priority_queue = [(0, i)]
    tiebreaker = rnd.uniform(0,.99)
    predecessor = {}
    
    
    while priority_queue: # until empty
        current_distance, current_node = heapq.heappop(priority_queue) #smallest dist.
        if current_distance > distances[current_node]:
            continue # skip if smaller distance already
        for neighbor in G.neighbors(current_node):
            weight = G[current_node][neighbor].get('weight', 1)  
            distance = current_distance + weight
            if distance < distances[neighbor]: # push to dist. dictionary
                distances[neighbor] = distance
                predecessor[neighbor] = current_node
                heapq.heappush(priority_queue, (distance, neighbor))
    shortest_path = []
    current_node = j
    while current_node in predecessor:
        shortest_path.insert(0, current_node) # j at the front
        current_node = predecessor[current_node]
    shortest_path.insert(0, i)

    if flag == 1:
        print(shortest_path)
    
        
    return distances[j] + tiebreaker
    

In [13]:
X = get_candidateEdges(Go) 
test = []
for i,j in X: 
    if (i,j) in Y:
        test.append("i")

print(len(test))

1900


In [14]:
def apply_predictors(G,Y):
    flag = 0
    X = get_candidateEdges(G)
    number_edges = len(X)
    dt = np.dtype([('i', 'U50'), ('j', 'U50'), ('tau', float), ('baseline', float), ('dp', float), ('jc', float), ('dij', float)])
    dat = np.zeros(number_edges, dtype=dt)

    for k,x in enumerate(X):
        i = x[0]
        j = x[1]
        tau = (i,j) in Y
        baseline = baseline_predictor()
        dp = degree_product(G,i,j)
        jc = jaccard_predictor(G, i,j)
        dij = dijkstra_predictor(G,i,j,flag)
        dat[k]['i'] = i
        dat[k]['j'] = j
        dat[k]['tau'] = tau
        dat[k]['baseline'] = baseline
        dat[k]['dp'] = dp
        dat[k]['jc'] = jc
        dat[k]['dij'] = dij
        
        
    return dat



In [15]:
dat = apply_predictors(Go,Y)
num_row = np.shape(dat)[0]
sdat = dat[dat[:6].argsort()[::-1][:num_row]]

for row in dat[:10]:  # Loop through the first 10 
    print(f" Nodes: ({row['i']}, {row['j']}) : missing? {row['tau']} | baseline: {row['baseline']} | degree product: {row['dp']} | jaccard: {row['jc']} | dijkstra: {row['dij']}")
    print("----------------------------------------------------------------------------------------------------------------------")

 Nodes: (AHRQ_AcquiredDeformities_DT, AHRQ_AbdominalHernia_DT) : missing? 0.0 | baseline: -0.2706973891659825 | degree product: 1728.00057203196 | jaccard: 0.22947802858020025 | dijkstra: 0.5397394253911969
----------------------------------------------------------------------------------------------------------------------
 Nodes: (AHRQ_DementiaAndOthDO_DT, AHRQ_AbdominalHernia_DT) : missing? 0.0 | baseline: -0.2676897300655936 | degree product: 1836.0000800663463 | jaccard: 0.20628771875944582 | dijkstra: 0.619128372616275
----------------------------------------------------------------------------------------------------------------------
 Nodes: (AHRQ_DOOfLipidMetabolism_DT, AHRQ_AbdominalHernia_DT) : missing? 0.0 | baseline: 0.7426679993739329 | degree product: 1728.0004171918167 | jaccard: 0.28391928279164397 | dijkstra: 0.0779122903455691
----------------------------------------------------------------------------------------------------------------------
 Nodes: (AHRQ_DOOfTeeth

In [16]:
df = pd.DataFrame(dat)
df = df.drop_duplicates(subset=['i','j'])
df_dij = df[['i','j','tau','dij']].copy()
df_baseline = df[['i','j','tau','baseline']].copy()
df_dp = df[['i','j','tau','dp']].copy()
df_jc = df[['i','j','tau','jc']].copy()

df_jc_sorted = df_jc.sort_values(by='jc',ascending=False).reset_index(drop=True)
df_dp_sorted = df_dp.sort_values('dp', ascending=False).reset_index(drop=True)
df_dij_sorted = df_dij.sort_values('dij', ascending=False).reset_index(drop=True)
df_baseline_sorted = df_baseline.sort_values('baseline', ascending=False).reset_index(drop=True)

In [17]:
# go through and add edges from predicted to Go for comparing centralities
length = len(Y)

top_predictions = df_jc_sorted[['i','j']].head(length)

top_predictions.head()

for index, row in top_predictions.iterrows():
  Go.add_edge(row['i'], row['j'])


In [18]:
print(top_10_weighted_edges)

                            source                      target    weight
7000      AHRQ_SpinalCordInjury_DT           AHRQ_Paralysis_DT  6.026605
3571            AHRQ_ImmunityDO_DT       AHRQ_OthInfections_DT  5.001760
6248             AHRQ_Paralysis_DT    AHRQ_SpinalCordInjury_DT  4.996151
1213    AHRQ_ChronicUlcerOfSkin_DT    AHRQ_SpinalCordInjury_DT  3.807992
1205    AHRQ_ChronicUlcerOfSkin_DT           AHRQ_Paralysis_DT  3.393637
3717    AHRQ_InfectiveArthritis_DT  AHRQ_ChronicUlcerOfSkin_DT  3.017421
6947      AHRQ_SpinalCordInjury_DT  AHRQ_ChronicUlcerOfSkin_DT  2.910909
6185             AHRQ_Paralysis_DT   AHRQ_CerebrovascularDs_DT  2.838896
6320  AHRQ_PathologicalFracture_DT        AHRQ_Osteoporosis_DT  2.648420
609     AHRQ_BacterialInfection_DT  AHRQ_InfectiveArthritis_DT  2.644675


In [19]:
def tabulate_TPR_FPR(df):
    # df = df.sort_values('dp', ascending=False).reset_index(drop=True) # so zig zag doesn't appear

    TP = df['tau'].sum()  #TP
    TN = len(df) - TP  #TN

    TPR = df['tau'].cumsum() / TP  
    FPR = (df.index + 1 - df['tau'].cumsum()) / TN # instead of df.index + 1 - TPR because FPR > 1
    return df.assign(TPR=TPR, FPR=FPR)  
        
    
        

In [20]:
def calculate_AUC(TPR, FPR):
    auc = np.trapz(TPR, FPR)
    return auc


In [21]:
# maybe make all of this data into one dataframe and make the chart from that, the legend will be easier
df_dp_new = tabulate_TPR_FPR(df_dp_sorted)
df_jc_new = tabulate_TPR_FPR(df_jc_sorted)
df_dij_new = tabulate_TPR_FPR(df_dij_sorted)
df_baseline_new = tabulate_TPR_FPR(df_baseline_sorted)

TPR_dp = df_dp_new['TPR']
FPR_dp = df_dp_new['FPR']

TPR_jc = df_jc_new['TPR']
FPR_jc = df_jc_new['FPR']

TPR_dij = df_dij_new['TPR']
FPR_dij = df_dij_new['FPR']

TPR_baseline = df_baseline_new['TPR']
FPR_baseline = df_baseline_new['FPR']

dp_chart = alt.Chart(df_dp_new).mark_line().encode(
    x = 'FPR',
    y = 'TPR'
).properties(
    width=500,
    height=500
)

jc_chart = alt.Chart(df_jc_new).mark_line(color='red').encode(
    x = 'FPR',
    y = 'TPR'
).properties(
    width=500,
    height=500
)
dij_chart = alt.Chart(df_dij_new).mark_line(color='green').encode(
    x = 'FPR',
    y = 'TPR'
).properties(
    width=500,
    height=500
)

baseline_chart = alt.Chart(df_baseline_new).mark_line(color='purple').encode(
    x = 'FPR',
    y = 'TPR'
).properties(
    width=500,
    height=500
)

line = pd.DataFrame({
    'FPR': [0, 1],
    'TPR': [0, 1],
})
random = alt.Chart(line).mark_line(color='grey',strokeDash=[3,5]).encode(
    x = 'FPR',
    y = 'TPR'
)

combination = dp_chart + random + jc_chart + dij_chart + baseline_chart

auc_dp = calculate_AUC(TPR_dp, FPR_dp)
print("AUC for degree product:", auc_dp)
print("-----------------------------------------")
auc_jc = calculate_AUC(TPR_jc, FPR_jc)
print("AUC for jaccard coeffienct:", auc_jc)
print("-----------------------------------------")
auc_dij = calculate_AUC(TPR_dij, FPR_dij)
print("AUC for dijkstra:", auc_dij)
print("-----------------------------------------")
auc_baseline = calculate_AUC(TPR_baseline, FPR_baseline)
print("AUC for baseline:", auc_baseline)

AUC for degree product: 0.8020327388223796
-----------------------------------------
AUC for jaccard coeffienct: 0.859750279681613
-----------------------------------------
AUC for dijkstra: 0.5094865431352631
-----------------------------------------
AUC for baseline: 0.5108848226111333


In [22]:
df_combined = pd.concat([df_dp_new.assign(algorithm='Degree Product'),
                         df_jc_new.assign(algorithm='Jaccard'),
                         df_dij_new.assign(algorithm='Dijkstra'),
                         df_baseline_new.assign(algorithm='Baseline')])

# Create the combination chart with legend
combination = alt.Chart(df_combined).mark_line().encode(
    x='FPR',
    y='TPR',
    color='algorithm:N'
).properties(
    width=500,
    height=500
)

line = pd.DataFrame({
    'FPR': [0, 1],
    'TPR': [0, 1],
})

# Add the reference line
random = alt.Chart(line).mark_line(color='grey', strokeDash=[3, 5]).encode(
    x='FPR',
    y='TPR'
)

# Combine all charts
combination = (combination + random).properties(
    title='ROC Curve '
)

# Print AUC for each algorithm
print("AUC for jaccard coefficient:", auc_jc)
print("-----------------------------------------")
print("AUC for degree product:", auc_dp)
print("-----------------------------------------")
print("AUC for baseline:", auc_baseline)
print("-----------------------------------------")
print("AUC for dijkstra:", auc_dij)


# Show the combination chart
combination

AUC for jaccard coefficient: 0.859750279681613
-----------------------------------------
AUC for degree product: 0.8020327388223796
-----------------------------------------
AUC for baseline: 0.5108848226111333
-----------------------------------------
AUC for dijkstra: 0.5094865431352631


alt.LayerChart(...)

In [23]:
degree_centrality = nx.degree_centrality(Go)
betweenness_centrality = nx.betweenness_centrality(Go)
closeness_centrality = nx.closeness_centrality(Go)


highest_degree_nodes = sorted(degree_centrality, key=degree_centrality.get, reverse=True)[:10]
highest_betweenness_nodes = sorted(betweenness_centrality, key=betweenness_centrality.get, reverse=True)[:10]
highest_closeness_nodes = sorted(closeness_centrality, key=closeness_centrality.get, reverse=True)[:10]

print("Top 10 nodes with highest degree centrality:", highest_degree_nodes)
print("------------------------------------------------------------------------")
print("Top 10 nodes with highest betweenness centrality:", highest_betweenness_nodes)
print("------------------------------------------------------------------------")
print("Top 10 nodes with highest closeness centrality:", highest_closeness_nodes)


Top 10 nodes with highest degree centrality: ['AHRQ_DOOfTeethAndJaw_DT', 'NEPEC_DXDRG_DT', 'AHRQ_OthInjuriesExternalCauses_D', 'AHRQ_OthInfections_DT', 'AHRQ_Burns_DT', 'AHRQ_DisOfTheHeart_DT', 'AHRQ_SkinInfections_DT', 'NEPEC_DXODep_DT', 'AHRQ_SuperficialInjury_DT', 'AHRQ_OthGIDO_DT']
------------------------------------------------------------------------
Top 10 nodes with highest betweenness centrality: ['AHRQ_PersonalityDO_DT', 'NEPEC_DXDRG_DT', 'AHRQ_OthInfections_DT', 'AHRQ_DisOfTheHeart_DT', 'AHRQ_LiverDs_DT', 'AHRQ_OthGIDO_DT', 'AHRQ_DisOfTheUrinarySystem_DT', 'AHRQ_Osteoporosis_DT', 'NEPEC_PTSD_DT', 'NEPEC_SCHZ_DT']
------------------------------------------------------------------------
Top 10 nodes with highest closeness centrality: ['AHRQ_Burns_DT', 'NEPEC_PTSD_DT', 'AHRQ_DementiaAndOthDO_DT', 'NEPEC_DXODep_DT', 'AHRQ_DOOfTeethAndJaw_DT', 'AHRQ_ImpulseControlDONEC_DT', 'NEPEC_AFBPDX_DT', 'AHRQ_JointDisorderTraumarelated_', 'AHRQ_SuperficialInjury_DT', 'AHRQ_Asthma_DT']


In [24]:
top_10 = df_jc_sorted[['i','j','jc']].head(15)
top_10 

i                                 j  \
0         AHRQ_RespiratoryFailure_DT     AHRQ_DisOfTheUrinarySystem_DT   
1      AHRQ_DisOfTheUrinarySystem_DT                   NEPEC_AFBPDX_DT   
2                     NEPEC_DXDRG_DT  AHRQ_CrushingInjuryOrInternalIn0   
3   AHRQ_CrushingInjuryOrInternalIn0                    NEPEC_DXDRG_DT   
4                  AHRQ_Poisoning_DT                    NEPEC_DXDRG_DT   
5      AHRQ_DisOfTheUrinarySystem_DT                 AHRQ_Fractures_DT   
6       AHRQ_DisOfWhiteBloodCells_DT                    NEPEC_DXDRG_DT   
7                     AHRQ_Anemia_DT                    NEPEC_DXDRG_DT   
8              AHRQ_DisOfTheHeart_DT     AHRQ_RespiratoryInfections_DT   
9         AHRQ_BacterialInfection_DT             AHRQ_OthInfections_DT   
10             AHRQ_DisOfTheHeart_DT  AHRQ_NoninfectiousGastroenterit0   
11     AHRQ_DisOfTheUrinarySystem_DT                     NEPEC_SCHZ_DT   
12                    NEPEC_DXDRG_DT  AHRQ_OthInjuriesExternalCauses_D   
13             AHRQ_DisOfTheHeart_DT                   AHRQ_OthGIDO_DT   
14             AHRQ_DisOfArteries_DT  AHRQ_NoninfectiousGastroenterit0   

          jc  
0   0.652504  
1   0.587816  
2   0.585213  
3   0.578982  
4   0.573833  
5   0.573481  
6   0.566170  
7   0.556092  
8   0.553250  
9   0.552205  
10  0.551020  
11  0.540264  
12  0.539956  
13  0.538463  
14  0.537724

In [25]:
print(top_10_weighted_edges)

                            source                      target    weight
7000      AHRQ_SpinalCordInjury_DT           AHRQ_Paralysis_DT  6.026605
3571            AHRQ_ImmunityDO_DT       AHRQ_OthInfections_DT  5.001760
6248             AHRQ_Paralysis_DT    AHRQ_SpinalCordInjury_DT  4.996151
1213    AHRQ_ChronicUlcerOfSkin_DT    AHRQ_SpinalCordInjury_DT  3.807992
1205    AHRQ_ChronicUlcerOfSkin_DT           AHRQ_Paralysis_DT  3.393637
3717    AHRQ_InfectiveArthritis_DT  AHRQ_ChronicUlcerOfSkin_DT  3.017421
6947      AHRQ_SpinalCordInjury_DT  AHRQ_ChronicUlcerOfSkin_DT  2.910909
6185             AHRQ_Paralysis_DT   AHRQ_CerebrovascularDs_DT  2.838896
6320  AHRQ_PathologicalFracture_DT        AHRQ_Osteoporosis_DT  2.648420
609     AHRQ_BacterialInfection_DT  AHRQ_InfectiveArthritis_DT  2.644675
